In [1]:
import requests
import pandas as pd
import numpy as np

http_proxy  = "http://proxy-web.micron.com:80"
https_proxy = "http://proxy-web.micron.com:80"
proxyDict = { 
    "http":http_proxy, 
    "https":https_proxy              
}

pd.set_option('display.max_rows', None) #show every row for pandas
pd.set_option('display.max_columns', None) #show every column for pandas

g_year = 108
g_season = 1
g_how_many_year = 3

In [2]:
# sii:上市, otc:上櫃
# TWSE之數據是至該季的累計數據而非單季數據, EX: Q3=> TWSE: Q1~Q3, 財報狗:Q3
def financial_statement(year, season, stocktype, type='綜合損益彙總表'):
    if year >= 1000:
        year -= 1911
        
    if type == '綜合損益彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb04'
    elif type == '資產負債彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb05'
    elif type == '營益分析彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb06'
    else:
        print('type does not match')
    
    r = requests.post(url, {
        'encodeURIComponent':1,
        'step':1,
        'firstin':1,
        'off':1,
        'TYPEK':stocktype,
        'year':str(year),
        'season':str(season),
    }, stream=True)#, verify=False)#, proxies=proxyDict)
    
    r.encoding = 'utf8'
    dfs = pd.read_html(r.text)
    
    
    for i, df in enumerate(dfs):
        df.columns = df.iloc[0]
        dfs[i] = df.iloc[1:]
        
    df = pd.concat(dfs).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df[u'公司代號'] != u'公司代號']
    df = df[~df[u'公司代號'].isnull()]
    
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_suffix.html
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_prefix.html
    suffix_format = "_{0}Q{1}".format(year, season)
    
    #return df.add_suffix(suffix_format)
    return df

In [3]:
def generate_df_for_stocktype(year, season, howmany_year_data, stocktype, title_name, with_col_name, sheettype):
    df = financial_statement(year, season, stocktype, type=sheettype)[[u'公司代號',u'公司名稱',with_col_name]]
    df.rename(columns = {df.columns[2]: '{0}_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

    for i in range(howmany_year_data*4):
        # calculate previous quarter data 107Q1 => we want the previous data is 106Q4 AND then 106Q3, 106Q2, 106Q1, 105Q4
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        #https://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.merge.html
        dfanother = financial_statement(year, season, stocktype, type=sheettype)[[u'公司代號',with_col_name]]    
        print(dfanother.columns[1])

        dfanother.rename(columns = {dfanother.columns[1]: '{0}_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

        df = df.merge(dfanother, on=u'公司代號', how='inner')
        print("year:", year)
        #print("year: {0}".format(year))
        print("season:", season)
        #print("season: {0}".format(season))

    return df

In [4]:
#Accumulate quarter data
df_eps_sii = generate_df_for_stocktype(g_year, g_season, g_how_many_year, 'sii', 'EPS', u'基本每股盈餘（元）', '綜合損益彙總表')

df_eps_sii

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



基本每股盈餘（元）
('year:', 107)
('season:', 4)
基本每股盈餘（元）
('year:', 107)
('season:', 3)
基本每股盈餘（元）
('year:', 107)
('season:', 2)
基本每股盈餘（元）
('year:', 107)
('season:', 1)
基本每股盈餘（元）
('year:', 106)
('season:', 4)
基本每股盈餘（元）
('year:', 106)
('season:', 3)
基本每股盈餘（元）
('year:', 106)
('season:', 2)
基本每股盈餘（元）
('year:', 106)
('season:', 1)
基本每股盈餘（元）
('year:', 105)
('season:', 4)
基本每股盈餘（元）
('year:', 105)
('season:', 3)
基本每股盈餘（元）
('year:', 105)
('season:', 2)
基本每股盈餘（元）
('year:', 105)
('season:', 1)


公司代號      公司名稱 EPS_108Q1 EPS_107Q4 EPS_107Q3 EPS_107Q2 EPS_107Q1  \
0    2801      彰化銀行      0.32      1.29      1.02      0.67      0.36   
1    2809      京城銀行      1.60      2.51      3.19      2.04      1.13   
2    2812      台中銀行      0.29      1.18      0.89      0.57      0.27   
3    2820        華票      0.23      0.99      0.78      0.54      0.25   
4    2834      臺灣企銀      0.34      1.19      0.94      0.64      0.30   
5    2836        高銀      0.17      0.46      0.35      0.21      0.01   
6    2838      聯邦銀行      0.26      1.07      0.86      0.53      0.26   
7    2845      遠東商銀      0.35      1.08      0.83      0.54      0.23   
8    2849      安泰銀行      0.31      1.26      0.83      0.55      0.26   
9    2855      統一證券      0.67      0.87      0.88      0.75      0.08   
10   6005       群益證      0.26      0.61      0.70      0.64      0.37   
11   6024       群益期      0.92      4.73      4.26      3.34      2.57   
12   1101        台泥      0.77      4.37      3.35      2.14      0.69   
13   1102        亞泥      0.93      3.54      2.96      1.98      0.60   
14   1103        嘉泥      0.20      1.09      1.37      0.62      0.24   
15   1104      環球水泥      0.24      1.62      1.16      0.63      0.01   
16   1108      幸福水泥     -0.07     -0.44     -0.12     -0.02     -0.01   
17   1109      信大水泥      0.37      2.38      1.40      0.69      0.34   
18   1110        東泥      0.05      0.12      0.16      0.10      0.03   
19   1201      味全公司      2.21      1.94      2.02      0.12      0.23   
20   1203      味王公司      0.50      1.82      1.44      0.86      0.31   
21   1210      大成長城      0.65      2.75      2.12      1.64      1.16   
22   1215      卜蜂企業      0.90      3.55      2.37      1.47      0.98   
23   1216        統一      0.93      3.07      2.61      1.72      0.75   
24   1217       愛之味      0.03      0.10      0.13      0.00      0.08   
25   1218      泰山企業      0.22      0.98      0.91      0.47      0.19   
26   1219      福壽實業      0.10     -0.03     -0.08      0.26      0.15   
27   1220        台榮      0.05      0.53      0.42      0.33      0.18   
28   1225       福懋油      0.36      1.17      0.79      0.72      0.38   
29   1227        佳格      0.87      3.25      2.40      1.21      0.82   
30   1229      聯華實業      1.00      2.35      1.84      1.24      0.57   
31   1231      聯華食品      0.66      3.26      2.22      1.27      0.84   
32   1232       大統益      1.86      5.67      3.90      2.69      1.23   
33   1233        天仁      0.49      1.93      1.56      1.04      0.43   
34   1234        黑松      0.41      1.73      1.43      0.72      0.30   
35   1235        興泰     -0.42      1.25      1.80      0.33      0.15   
36   1236      宏亞食品      0.08      0.12     -0.33     -0.16      0.31   
37   1256   鮮活果汁-KY      2.96     14.35     12.47      7.21      2.13   
38   1262     綠悅-KY     -0.71     -2.72     -1.66     -1.13     -0.14   
39   1301        台塑      1.28      7.78      7.42      4.56      1.87   
40   1303      南亞塑膠      0.64      6.65      6.10      3.80      1.70   
41   1304        台聚      0.24      0.50      0.60      0.49      0.24   
42   1305        華夏      0.36      2.52      2.30      1.82      1.10   
43   1307      三芳化工      0.25      0.76      0.59      0.41      0.26   
44   1308        亞聚      0.25      0.52      0.48      0.29      0.16   
45   1309      台達化工      0.60      0.63      1.17      1.17      0.58   
46   1310        台苯      0.63      2.30      2.20      1.40      0.75   
47   1312      國喬石化      0.65      3.26      3.00      1.96      1.08   
48   1313        聯成     -0.11      0.59      0.68      0.46      0.37   
49   1314       中石化      0.11      1.59      1.47      0.86      0.41   
50   1315      達新工業      0.02      1.20      1.47     -0.09     -0.04   
51   1316        上曜     -0.31      1.39      2.24      1.99      1.25   
52   1319        東陽      0.85      3.26      2.44      1.82      0.84   
53   1321        大洋      0.14     -0.33      0.09     -0.15    

In [5]:
#Every single quarter data

#Each Dataframe object has a member variable shape i.e. a tuple that contains dimensions of a dataframe like,
#(Number_of_index, Number_of_columns)
#idx = df_eps_sii.columns # the column index
#idx = df_eps_sii.index # the row index
numOfRows_s = df_eps_sii.shape[0] #len(df_eps_sii) #len(df_eps_sii.index)
numOfColumns_s = df_eps_sii.shape[1] #len(df_eps_sii.columns)
headNameOfColumns_s = df_eps_sii.columns

print(numOfColumns_s)
df_eps_sii

for row_index_s in range(0, numOfRows_s):
    for col_index_s in range(0, numOfColumns_s):
        #print(df_eps_sii.columns.values[col_index].find('Q1')) # index of match string
        #print("Q1" in df_eps_sii.columns.values[col_index]) # True OR False
        #How to Check if a Python String Contains Another String?
        if ("Q1" in df_eps_sii.columns.values[col_index_s]): # if (df_eps_sii.columns.values[col_index].find('Q1') > -1):
            continue
        else:
            if (u"公司代號" in df_eps_sii.columns.values[col_index_s]):
                continue
            elif (u"公司名稱" in df_eps_sii.columns.values[col_index_s]):
                continue
            elif (col_index_s == numOfColumns_s-1):
                continue
            else:
                df_eps_sii.iloc[row_index_s, col_index_s] = float(df_eps_sii.iloc[row_index_s, col_index_s]) - float(df_eps_sii.iloc[row_index_s, col_index_s+1])

df_eps_sii              

15


公司代號      公司名稱 EPS_108Q1 EPS_107Q4 EPS_107Q3 EPS_107Q2 EPS_107Q1  \
0    2801      彰化銀行      0.32      0.27      0.35      0.31      0.36   
1    2809      京城銀行      1.60     -0.68      1.15      0.91      1.13   
2    2812      台中銀行      0.29      0.29      0.32       0.3      0.27   
3    2820        華票      0.23      0.21      0.24      0.29      0.25   
4    2834      臺灣企銀      0.34      0.25       0.3      0.34      0.30   
5    2836        高銀      0.17      0.11      0.14       0.2      0.01   
6    2838      聯邦銀行      0.26      0.21      0.33      0.27      0.26   
7    2845      遠東商銀      0.35      0.25      0.29      0.31      0.23   
8    2849      安泰銀行      0.31      0.43      0.28      0.29      0.26   
9    2855      統一證券      0.67     -0.01      0.13      0.67      0.08   
10   6005       群益證      0.26     -0.09      0.06      0.27      0.37   
11   6024       群益期      0.92      0.47      0.92      0.77      2.57   
12   1101        台泥      0.77      1.02      1.21      1.45      0.69   
13   1102        亞泥      0.93      0.58      0.98      1.38      0.60   
14   1103        嘉泥      0.20     -0.28      0.75      0.38      0.24   
15   1104      環球水泥      0.24      0.46      0.53      0.62      0.01   
16   1108      幸福水泥     -0.07     -0.32      -0.1     -0.01     -0.01   
17   1109      信大水泥      0.37      0.98      0.71      0.35      0.34   
18   1110        東泥      0.05     -0.04      0.06      0.07      0.03   
19   1201      味全公司      2.21     -0.08       1.9     -0.11      0.23   
20   1203      味王公司      0.50      0.38      0.58      0.55      0.31   
21   1210      大成長城      0.65      0.63      0.48      0.48      1.16   
22   1215      卜蜂企業      0.90      1.18       0.9      0.49      0.98   
23   1216        統一      0.93      0.46      0.89      0.97      0.75   
24   1217       愛之味      0.03     -0.03      0.13     -0.08      0.08   
25   1218      泰山企業      0.22      0.07      0.44      0.28      0.19   
26   1219      福壽實業      0.10      0.05     -0.34      0.11      0.15   
27   1220        台榮      0.05      0.11      0.09      0.15      0.18   
28   1225       福懋油      0.36      0.38      0.07      0.34      0.38   
29   1227        佳格      0.87      0.85      1.19      0.39      0.82   
30   1229      聯華實業      1.00      0.51       0.6      0.67      0.57   
31   1231      聯華食品      0.66      1.04      0.95      0.43      0.84   
32   1232       大統益      1.86      1.77      1.21      1.46      1.23   
33   1233        天仁      0.49      0.37      0.52      0.61      0.43   
34   1234        黑松      0.41       0.3      0.71      0.42      0.30   
35   1235        興泰     -0.42     -0.55      1.47      0.18      0.15   
36   1236      宏亞食品      0.08      0.45     -0.17     -0.47      0.31   
37   1256   鮮活果汁-KY      2.96      1.88      5.26      5.08      2.13   
38   1262     綠悅-KY     -0.71     -1.06     -0.53     -0.99     -0.14   
39   1301        台塑      1.28      0.36      2.86      2.69      1.87   
40   1303      南亞塑膠      0.64      0.55       2.3       2.1      1.70   
41   1304        台聚      0.24      -0.1      0.11      0.25      0.24   
42   1305        華夏      0.36      0.22      0.48      0.72      1.10   
43   1307      三芳化工      0.25      0.17      0.18      0.15      0.26   
44   1308        亞聚      0.25      0.04      0.19      0.13      0.16   
45   1309      台達化工      0.60     -0.54         0      0.59      0.58   
46   1310        台苯      0.63       0.1       0.8      0.65      0.75   
47   1312      國喬石化      0.65      0.26      1.04      0.88      1.08   
48   1313        聯成     -0.11     -0.09      0.22      0.09      0.37   
49   1314       中石化      0.11      0.12      0.61      0.45      0.41   
50   1315      達新工業      0.02     -0.27      1.56     -0.05     -0.04   
51   1316        上曜     -0.31     -0.85      0.25      0.74      1.25   
52   1319        東陽      0.85      0.82      0.62      0.98      0.84   
53   1321        大洋      0.14     -0.42      0.24     -0.33    

In [6]:
#Accumulate quarter data
df_eps_otc = generate_df_for_stocktype(g_year, g_season, g_how_many_year, 'otc', 'EPS', u'基本每股盈餘（元）', '綜合損益彙總表')

df_eps_otc

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



基本每股盈餘（元）
('year:', 107)
('season:', 4)
基本每股盈餘（元）
('year:', 107)
('season:', 3)
基本每股盈餘（元）
('year:', 107)
('season:', 2)
基本每股盈餘（元）
('year:', 107)
('season:', 1)
基本每股盈餘（元）
('year:', 106)
('season:', 4)
基本每股盈餘（元）
('year:', 106)
('season:', 3)
基本每股盈餘（元）
('year:', 106)
('season:', 2)
基本每股盈餘（元）
('year:', 106)
('season:', 1)
基本每股盈餘（元）
('year:', 105)
('season:', 4)
基本每股盈餘（元）
('year:', 105)
('season:', 3)
基本每股盈餘（元）
('year:', 105)
('season:', 2)
基本每股盈餘（元）
('year:', 105)
('season:', 1)


公司代號    公司名稱 EPS_108Q1 EPS_107Q4 EPS_107Q3 EPS_107Q2 EPS_107Q1 EPS_106Q4  \
0    6015    宏遠證券      0.29     -1.20     -0.72      0.07     -0.08      0.57   
1    6016    康和證券      0.09     -0.45     -0.23     -0.08     -0.26      1.15   
2    6020     大展證      0.25      0.01      0.12      0.30     -0.03      0.95   
3    6021     大慶證      0.00      0.64      0.69      0.36      0.13      0.55   
4    6023    元大期貨      1.09      4.31      2.95      1.86      0.89      3.76   
5    6026    福邦證券      0.39      0.15      0.46      0.46      0.34      2.00   
6    1258   其祥-KY     -0.40     -4.05     -3.18      0.22      0.17      1.26   
7    1259      安心      0.87      4.36      3.66      2.05      0.80      5.23   
8    1264      德麥      3.20     13.27     10.00      6.32      2.85     13.41   
9    1333     恩得利     -0.33     -1.44     -1.31     -1.81     -0.91     -1.93   
10   1336      台翰      0.03      1.28      1.06      0.57      0.14      1.44   
11   1565    精華光學      7.68     33.07     24.75     16.48      7.00     31.52   
12   1566      捷邦      0.36      0.66      0.61      0.31      0.05      1.03   
13   1569      濱川      0.11      0.35      0.18      0.13      0.03      2.61   
14   1570    力肯實業      0.18      1.62      1.17      0.64      0.19      1.48   
15   1580    新麥企業      1.48      9.43      6.25      3.68      0.98     11.01   
16   1584    精剛精密     -0.16     -0.84     -0.54     -0.50     -0.40     -0.96   
17   1586    和勤精機     -0.46      1.36      1.34      0.76      0.20      0.42   
18   1591   駿吉-KY      0.34      1.44      1.03      0.41      0.01      0.06   
19   1593      祺驊      0.81      3.80      2.64      1.20      0.31      3.77   
20   1595    川寶科技      0.19      4.18      3.31      1.91      0.34      7.12   
21   1597      直得      0.61      6.40      5.11      3.41      1.69      4.03   
22   1599     宏佳騰      0.88      3.59      2.62      0.13     -0.19      2.40   
23   1742      台蠟      0.22     -1.93     -1.90     -1.27     -0.34      0.12   
24   1752      南光      0.35      1.00      0.77      0.67      0.37      1.84   
25   1777      生泰      1.34      5.12      3.85      2.89      0.86      1.99   
26   1781    合世生醫     -0.38     -0.81     -0.61     -0.49     -0.36     -1.44   
27   1784    訊聯生技      0.18      0.49      0.35      0.27      0.19     -0.13   
28   1785     光洋科      0.39      0.98      1.29      0.84      0.34      0.33   
29   1787     福盈科      0.45      1.60      1.18      0.84      0.34      1.98   
30   1788    杏昌生技      1.81      6.96      5.13      3.65      1.70      7.17   
31   1795    美時製藥      1.16      0.42      0.11     -0.17      0.07      0.09   
32   1799      易威     -0.60     -2.45     -1.52     -1.18     -0.54     -3.50   
33   1813     寶利徠      0.44      1.37      1.12      0.94      0.18      0.05   
34   1815    富喬工業      0.15      0.97      0.90      0.60      0.34      1.16   
35   2035    唐榮公司      0.43     -4.12     -2.12     -0.70     -0.47      0.69   
36   2061      風青      0.02     -0.32     -0.10      0.22      0.14      0.50   
37   2063      世鎧      0.88      3.67      2.92      1.74      0.82      2.63   
38   2064      晉椿     -0.12      1.02      0.74      0.71      0.01      0.41   
39   2066      世德      1.32      4.21      3.50      2.71      0.27      4.67   
40   2067      嘉鋼     -0.20      1.42      1.03      0.58      0.10     -1.38   
41   2221    大甲永和      0.79      3.35      2.67      1.60      0.66      2.06   
42   2230      泰茂      0.04      0.25      0.20      0.08     -0.24     -0.44   
43   2233      宇隆      1.71      7.05      5.54      4.70      1.54      8.05   
44   2235      謚源      0.93      3.01      2.24      1.33      0.55      3.48   
45   2596    綠意開發     -0.15      3.64      3.69      3.81      2.18      2.72   
46   2640     大車隊      0.86      4.51      3.50      2.45      1.33      4.56   
47   2641    正德海運      0.12      0.62      0.49      0.28      0.14     -2.76   
48   2643      捷迅      0.55      2.8

In [7]:
#Every single quarter data

#Each Dataframe object has a member variable shape i.e. a tuple that contains dimensions of a dataframe like,
#(Number_of_index, Number_of_columns)
#idx = df_eps_otc.columns # the column index
#idx = df_eps_otc.index # the row index
numOfRows_o = df_eps_otc.shape[0] #len(df_eps_otc) #len(df_eps_otc.index)
numOfColumns_o = df_eps_otc.shape[1] #len(df_eps_otc.columns)
headNameOfColumns_o = df_eps_otc.columns

print(numOfColumns_o)
df_eps_otc

for row_index_o in range(0, numOfRows_o):
    for col_index_o in range(0, numOfColumns_o):
        #print(df_eps_otc.columns.values[col_index].find('Q1')) # index of match string
        #print("Q1" in df_eps_otc.columns.values[col_index]) # True OR False
        #How to Check if a Python String Contains Another String?
        if ("Q1" in df_eps_otc.columns.values[col_index_o]): # if (df_eps_otc.columns.values[col_index].find('Q1') > -1):
            continue
        else:
            if (u"公司代號" in df_eps_otc.columns.values[col_index_o]):
                continue
            elif (u"公司名稱" in df_eps_otc.columns.values[col_index_o]):
                continue
            elif (col_index_o == numOfColumns_o-1):
                continue
            else:
                df_eps_otc.iloc[row_index_o, col_index_o] = float(df_eps_otc.iloc[row_index_o, col_index_o]) - float(df_eps_otc.iloc[row_index_o, col_index_o+1])

df_eps_otc              

15


公司代號    公司名稱 EPS_108Q1 EPS_107Q4 EPS_107Q3 EPS_107Q2 EPS_107Q1 EPS_106Q4  \
0    6015    宏遠證券      0.29     -0.48     -0.79      0.15     -0.08      0.06   
1    6016    康和證券      0.09     -0.22     -0.15      0.18     -0.26      0.39   
2    6020     大展證      0.25     -0.11     -0.18      0.33     -0.03      0.09   
3    6021     大慶證      0.00     -0.05      0.33      0.23      0.13      0.08   
4    6023    元大期貨      1.09      1.36      1.09      0.97      0.89      1.12   
5    6026    福邦證券      0.39     -0.31         0      0.12      0.34      0.48   
6    1258   其祥-KY     -0.40     -0.87      -3.4      0.05      0.17      -0.2   
7    1259      安心      0.87       0.7      1.61      1.25      0.80      0.73   
8    1264      德麥      3.20      3.27      3.68      3.47      2.85      3.39   
9    1333     恩得利     -0.33     -0.13       0.5      -0.9     -0.91     -0.46   
10   1336      台翰      0.03      0.22      0.49      0.43      0.14      0.31   
11   1565    精華光學      7.68      8.32      8.27      9.48      7.00      7.84   
12   1566      捷邦      0.36      0.05       0.3      0.26      0.05      0.34   
13   1569      濱川      0.11      0.17      0.05       0.1      0.03       0.7   
14   1570    力肯實業      0.18      0.45      0.53      0.45      0.19       0.2   
15   1580    新麥企業      1.48      3.18      2.57       2.7      0.98      3.09   
16   1584    精剛精密     -0.16      -0.3     -0.04      -0.1     -0.40     -0.39   
17   1586    和勤精機     -0.46      0.02      0.58      0.56      0.20      0.17   
18   1591   駿吉-KY      0.34      0.41      0.62       0.4      0.01     -0.03   
19   1593      祺驊      0.81      1.16      1.44      0.89      0.31      1.16   
20   1595    川寶科技      0.19      0.87       1.4      1.57      0.34      4.69   
21   1597      直得      0.61      1.29       1.7      1.72      1.69      1.43   
22   1599     宏佳騰      0.88      0.97      2.49      0.32     -0.19      1.11   
23   1742      台蠟      0.22     -0.03     -0.63     -0.93     -0.34      0.05   
24   1752      南光      0.35      0.23       0.1       0.3      0.37      0.51   
25   1777      生泰      1.34      1.27      0.96      2.03      0.86      0.47   
26   1781    合世生醫     -0.38      -0.2     -0.12     -0.13     -0.36      -0.4   
27   1784    訊聯生技      0.18      0.14      0.08      0.08      0.19      0.02   
28   1785     光洋科      0.39     -0.31      0.45       0.5      0.34      0.17   
29   1787     福盈科      0.45      0.42      0.34       0.5      0.34      0.49   
30   1788    杏昌生技      1.81      1.83      1.48      1.95      1.70      2.08   
31   1795    美時製藥      1.16      0.31      0.28     -0.24      0.07      0.04   
32   1799      易威     -0.60     -0.93     -0.34     -0.64     -0.54     -0.88   
33   1813     寶利徠      0.44      0.25      0.18      0.76      0.18      -0.2   
34   1815    富喬工業      0.15      0.07       0.3      0.26      0.34         0   
35   2035    唐榮公司      0.43        -2     -1.42     -0.23     -0.47     -0.09   
36   2061      風青      0.02     -0.22     -0.32      0.08      0.14      0.18   
37   2063      世鎧      0.88      0.75      1.18      0.92      0.82      0.59   
38   2064      晉椿     -0.12      0.28      0.03       0.7      0.01      0.13   
39   2066      世德      1.32      0.71      0.79      2.44      0.27      1.13   
40   2067      嘉鋼     -0.20      0.39      0.45      0.48      0.10      0.03   
41   2221    大甲永和      0.79      0.68      1.07      0.94      0.66      0.69   
42   2230      泰茂      0.04      0.05      0.12      0.32     -0.24         0   
43   2233      宇隆      1.71      1.51      0.84      3.16      1.54      2.14   
44   2235      謚源      0.93      0.77      0.91      0.78      0.55      0.33   
45   2596    綠意開發     -0.15     -0.05     -0.12      1.63      2.18      1.48   
46   2640     大車隊      0.86      1.01      1.05      1.12      1.33      1.04   
47   2641    正德海運      0.12      0.13      0.21      0.14      0.14     -2.74   
48   2643      捷迅      0.55      0.9

In [8]:
#Database-style DataFrame joining/merging: join, merge
#Concatenating objects: concat, append

#ignore_index = True 可以忽略合併時舊的 index 欄位，改採用自動產生的 index
df_eps = pd.concat([df_eps_sii,df_eps_otc],axis=0, ignore_index=True)

df_eps

公司代號      公司名稱 EPS_108Q1 EPS_107Q4 EPS_107Q3 EPS_107Q2 EPS_107Q1  \
0     2801      彰化銀行      0.32      0.27      0.35      0.31      0.36   
1     2809      京城銀行      1.60     -0.68      1.15      0.91      1.13   
2     2812      台中銀行      0.29      0.29      0.32       0.3      0.27   
3     2820        華票      0.23      0.21      0.24      0.29      0.25   
4     2834      臺灣企銀      0.34      0.25       0.3      0.34      0.30   
5     2836        高銀      0.17      0.11      0.14       0.2      0.01   
6     2838      聯邦銀行      0.26      0.21      0.33      0.27      0.26   
7     2845      遠東商銀      0.35      0.25      0.29      0.31      0.23   
8     2849      安泰銀行      0.31      0.43      0.28      0.29      0.26   
9     2855      統一證券      0.67     -0.01      0.13      0.67      0.08   
10    6005       群益證      0.26     -0.09      0.06      0.27      0.37   
11    6024       群益期      0.92      0.47      0.92      0.77      2.57   
12    1101        台泥      0.77      1.02      1.21      1.45      0.69   
13    1102        亞泥      0.93      0.58      0.98      1.38      0.60   
14    1103        嘉泥      0.20     -0.28      0.75      0.38      0.24   
15    1104      環球水泥      0.24      0.46      0.53      0.62      0.01   
16    1108      幸福水泥     -0.07     -0.32      -0.1     -0.01     -0.01   
17    1109      信大水泥      0.37      0.98      0.71      0.35      0.34   
18    1110        東泥      0.05     -0.04      0.06      0.07      0.03   
19    1201      味全公司      2.21     -0.08       1.9     -0.11      0.23   
20    1203      味王公司      0.50      0.38      0.58      0.55      0.31   
21    1210      大成長城      0.65      0.63      0.48      0.48      1.16   
22    1215      卜蜂企業      0.90      1.18       0.9      0.49      0.98   
23    1216        統一      0.93      0.46      0.89      0.97      0.75   
24    1217       愛之味      0.03     -0.03      0.13     -0.08      0.08   
25    1218      泰山企業      0.22      0.07      0.44      0.28      0.19   
26    1219      福壽實業      0.10      0.05     -0.34      0.11      0.15   
27    1220        台榮      0.05      0.11      0.09      0.15      0.18   
28    1225       福懋油      0.36      0.38      0.07      0.34      0.38   
29    1227        佳格      0.87      0.85      1.19      0.39      0.82   
30    1229      聯華實業      1.00      0.51       0.6      0.67      0.57   
31    1231      聯華食品      0.66      1.04      0.95      0.43      0.84   
32    1232       大統益      1.86      1.77      1.21      1.46      1.23   
33    1233        天仁      0.49      0.37      0.52      0.61      0.43   
34    1234        黑松      0.41       0.3      0.71      0.42      0.30   
35    1235        興泰     -0.42     -0.55      1.47      0.18      0.15   
36    1236      宏亞食品      0.08      0.45     -0.17     -0.47      0.31   
37    1256   鮮活果汁-KY      2.96      1.88      5.26      5.08      2.13   
38    1262     綠悅-KY     -0.71     -1.06     -0.53     -0.99     -0.14   
39    1301        台塑      1.28      0.36      2.86      2.69      1.87   
40    1303      南亞塑膠      0.64      0.55       2.3       2.1      1.70   
41    1304        台聚      0.24      -0.1      0.11      0.25      0.24   
42    1305        華夏      0.36      0.22      0.48      0.72      1.10   
43    1307      三芳化工      0.25      0.17      0.18      0.15      0.26   
44    1308        亞聚      0.25      0.04      0.19      0.13      0.16   
45    1309      台達化工      0.60     -0.54         0      0.59      0.58   
46    1310        台苯      0.63       0.1       0.8      0.65      0.75   
47    1312      國喬石化      0.65      0.26      1.04      0.88      1.08   
48    1313        聯成     -0.11     -0.09      0.22      0.09      0.37   
49    1314       中石化      0.11      0.12      0.61      0.45      0.41   
50    1315      達新工業      0.02     -0.27      1.56     -0.05     -0.04   
51    1316        上曜     -0.31     -0.85      0.25      0.74      1.25   
52    1319        東陽      0.85      0.82      0.62      0.98      0.84   
53    1321

In [9]:
#檢查column資料型態

#df_eps.info() #non-null object
#df_eps.dtypes #object
#df_eps.applymap(np.isreal) #all False
'''
公司代號              int64
公司名稱             object
EPS(%)_107Q1    float64
EPS(%)_106Q4    float64
EPS(%)_106Q3    float64
EPS(%)_106Q2    float64
EPS(%)_106Q1    float64
EPS(%)_105Q4    float64
EPS(%)_105Q3    float64
EPS(%)_105Q2    float64
EPS(%)_105Q1    float64
EPS(%)_104Q4    float64
EPS(%)_104Q3    float64
EPS(%)_104Q2    float64
EPS(%)_104Q1    float64
dtype: object
'''

df_eps = df_eps.convert_objects(convert_numeric=True) #轉成float型態方便後續處理

df_eps.convert_objects(convert_numeric=True).dtypes #轉成float型態方便後續處理

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:25: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:27: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


公司代號           int64
公司名稱          object
EPS_108Q1    float64
EPS_107Q4    float64
EPS_107Q3    float64
EPS_107Q2    float64
EPS_107Q1    float64
EPS_106Q4    float64
EPS_106Q3    float64
EPS_106Q2    float64
EPS_106Q1    float64
EPS_105Q4    float64
EPS_105Q3    float64
EPS_105Q2    float64
EPS_105Q1    float64
dtype: object

In [10]:
def isFloat(element):  
    try:
        float(element)
        return True
    except ValueError:
        return False

In [11]:
def growth_func(row, year, season):
    previous_year = year - 1
    #判斷是否為文字而非數字
    if(isFloat(row['EPS_{0}Q{1}'.format(year, season)]) == True):
        subsequent_value = float(row['EPS_{0}Q{1}'.format(year, season)])
        previous_value = float(row['EPS_{0}Q{1}'.format(previous_year, season)])
   
        if(previous_value == 0):
            result = ((subsequent_value - previous_value)/np.abs(subsequent_value))*100
        else:
            result = ((subsequent_value - previous_value)/np.abs(previous_value))*100            
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
     
    else:
        return 'NoValue'

In [12]:
def ma2q_growth_func(row, year, season):
    #判斷是否為文字而非數字
    if(isFloat(row['EPS_{0}Q{1}'.format(year, season)]) == True):
        previous_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        subsequent_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        
        result = ((subsequent_value + previous_value)/2)
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
    
    else:
        return 'NoValue'

In [13]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4)):
    df_eps['Growth_{0}Q{1}'.format(year, season)] = df_eps.apply (lambda row: growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:9: RuntimeWarning: invalid value encountered in double_scalars
  if __name__ == '__main__':


In [14]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4-1)):
    df_eps['2QMAGrowth_{0}Q{1}'.format(year, season)] = df_eps.apply (lambda row: ma2q_growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [15]:
def get_basic_info_for_ftock(stocktype):

    #get basic info of company
    '''
    抓取上市櫃股票的代號、名稱...等資料。
    上市
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=2
    上櫃
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=4
    '''
    #http://bloggerkaiweng.blogspot.com/2016/09/python.html

    if(stocktype == 'sii'):
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=2'
    else:
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=4'
    
    r = requests.get(url, stream=True)#, verify=False, proxies=proxyDict)
    r.encoding = 'big5hkscs'
    dfshow = pd.read_html(r.text, header=None)

    for i, df in enumerate(dfshow):
        df.columns = df.iloc[0]
        dfshow[i] = df.iloc[1:]

    df = pd.concat(dfshow).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df[u'有價證券代號及名稱'] != u'股票']
    df = df[~df[u'有價證券代號及名稱'].isnull()]
    df = df.reset_index(drop=True)
    
    newdf=df[df[u'產業別'] > '0']
    del newdf[u'國際證券辨識號碼(ISIN Code)'],newdf['CFICode'],newdf[u'備註']

    df2=newdf[u'有價證券代號及名稱'].str.split(u' ', expand=True)
    df2 = df2.reset_index(drop=True)
    newdf = newdf.reset_index(drop=True)
    for i in df2.index:
        if u'　' in df2.iat[i,0]:
            df2.iat[i,1]=df2.iat[i,0].split(u'　')[1]
            df2.iat[i,0]=df2.iat[i,0].split(u'　')[0]
    newdf=df2.join(newdf)
    newdf=newdf.rename(columns = {0:u'公司代號',1:u'股票名稱'})
    del newdf[u'有價證券代號及名稱']

    return newdf

In [16]:
df_basicinfo_sii = get_basic_info_for_ftock('sii').convert_objects(convert_numeric=True) #轉成float型態
df_basicinfo_otc = get_basic_info_for_ftock('otc').convert_objects(convert_numeric=True) #轉成float型態

df_basicinfo = pd.concat([df_basicinfo_sii,df_basicinfo_otc],axis=0, ignore_index=True)
#df_eps_basicinfo_sii.dtypes
#df_eps_basicinfo_otc

df_eps = df_eps.merge(df_basicinfo, on=u'公司代號', how='inner')

df_eps

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  """Entry point for launching an IPython kernel.
C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:2: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  


公司代號      公司名稱  EPS_108Q1  EPS_107Q4  EPS_107Q3  EPS_107Q2  EPS_107Q1  \
0     2801      彰化銀行       0.32       0.27       0.35       0.31       0.36   
1     2809      京城銀行       1.60      -0.68       1.15       0.91       1.13   
2     2812      台中銀行       0.29       0.29       0.32       0.30       0.27   
3     2820        華票       0.23       0.21       0.24       0.29       0.25   
4     2834      臺灣企銀       0.34       0.25       0.30       0.34       0.30   
5     2836        高銀       0.17       0.11       0.14       0.20       0.01   
6     2838      聯邦銀行       0.26       0.21       0.33       0.27       0.26   
7     2845      遠東商銀       0.35       0.25       0.29       0.31       0.23   
8     2849      安泰銀行       0.31       0.43       0.28       0.29       0.26   
9     2855      統一證券       0.67      -0.01       0.13       0.67       0.08   
10    6005       群益證       0.26      -0.09       0.06       0.27       0.37   
11    6024       群益期       0.92       0.47       0.92       0.77       2.57   
12    1101        台泥       0.77       1.02       1.21       1.45       0.69   
13    1102        亞泥       0.93       0.58       0.98       1.38       0.60   
14    1103        嘉泥       0.20      -0.28       0.75       0.38       0.24   
15    1104      環球水泥       0.24       0.46       0.53       0.62       0.01   
16    1108      幸福水泥      -0.07      -0.32      -0.10      -0.01      -0.01   
17    1109      信大水泥       0.37       0.98       0.71       0.35       0.34   
18    1110        東泥       0.05      -0.04       0.06       0.07       0.03   
19    1201      味全公司       2.21      -0.08       1.90      -0.11       0.23   
20    1203      味王公司       0.50       0.38       0.58       0.55       0.31   
21    1210      大成長城       0.65       0.63       0.48       0.48       1.16   
22    1215      卜蜂企業       0.90       1.18       0.90       0.49       0.98   
23    1216        統一       0.93       0.46       0.89       0.97       0.75   
24    1217       愛之味       0.03      -0.03       0.13      -0.08       0.08   
25    1218      泰山企業       0.22       0.07       0.44       0.28       0.19   
26    1219      福壽實業       0.10       0.05      -0.34       0.11       0.15   
27    1220        台榮       0.05       0.11       0.09       0.15       0.18   
28    1225       福懋油       0.36       0.38       0.07       0.34       0.38   
29    1227        佳格       0.87       0.85       1.19       0.39       0.82   
30    1229      聯華實業       1.00       0.51       0.60       0.67       0.57   
31    1231      聯華食品       0.66       1.04       0.95       0.43       0.84   
32    1232       大統益       1.86       1.77       1.21       1.46       1.23   
33    1233        天仁       0.49       0.37       0.52       0.61       0.43   
34    1234        黑松       0.41       0.30       0.71       0.42       0.30   
35    1235        興泰      -0.42      -0.55       1.47       0.18       0.15   
36    1236      宏亞食品       0.08       0.45      -0.17      -0.47       0.31   
37    1256   鮮活果汁-KY       2.96       1.88       5.26       5.08       2.13   
38    1262     綠悅-KY      -0.71      -1.06      -0.53      -0.99      -0.14   
39    1301        台塑       1.28       0.36       2.86       2.69       1.87   
40    1303      南亞塑膠       0.64       0.55       2.30       2.10       1.70   
41    1304        台聚       0.24      -0.10       0.11       0.25       0.24   
42    1305        華夏       0.36       0.22       0.48       0.72       1.10   
43    1307      三芳化工       0.25       0.17       0.18       0.15       0.26   
44    1308        亞聚       0.25       0.04       0.19       0.13       0.16   
45    1309      台達化工       0.60      -0.54       0.00       0.59       0.58   
46    1310        台苯       0.63       0.10       0.80       0.65       0.75   
47    1312      國喬石化       0.65       0.26       1.04       0.88       1.08   
48    1313        聯成      -0.11      -0.09       0.22       0.09       0.37   
49    1314       中石化       0.11       0.12       0.61   

In [17]:
# pandas styling
def color_white(val):
    """
    Takes a scalar and returns a string with
    the css property `'color: red'` for negative
    strings, black otherwise.
    """
    color = 'white'
    return 'color: %s' % color

def background_color(val):    
    if float(val) < 0:
        backgroundcolor = '#ff0000'
    elif float(val) < 10:
        backgroundcolor = '#f47721'
    elif float(val) < 20:
        backgroundcolor = '#ffdd00'
    elif float(val) < 30:
        backgroundcolor = '#5ecc62'
    else:
        backgroundcolor = '#00ad45'
    return 'background-color: %s' % backgroundcolor

"""
Export to Excel
Some support is available for exporting styled DataFrames to Excel worksheets using the OpenPyXL or XlsxWriter engines. 
CSS2.2 properties handled include:

* background-color
* border-style, border-width, border-color and their {top, right, bottom, left variants}
* color
* font-family
* font-style
* font-weight
* text-align
* text-decoration
* vertical-align
* white-space: nowrap
"""
def font_family(val):    
    fontfamily = 'Calibri'
    return 'font-family: %s' % fontfamily

def font_size(val):    
    fontsize = '10pt'
    return 'font-size: %s' % fontsize

In [18]:
# styled dataframe can use .to_excel('Styled_Basic_EPS.xlsx', engine='openpyxl') to export excel with style
year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
columns_name = []
for i in range(int(howmany_year_data*4-4)):
    columns_name.append('Growth_{0}Q{1}'.format(year, season))
    columns_name.append('2QMAGrowth_{0}Q{1}'.format(year, season))
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

print(columns_name)
# the cell’s style depends only on it’s own value. That means we should use the Styler.applymap method which works elementwise.
# Now suppose you wanted to highlight the maximum value in each column. We can’t use .applymap anymore since that operated elementwise. Instead, we’ll turn to .apply which operates columnwise (or rowwise using the axis keyword).
#df_eps.style.applymap(color_negative_red, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).applymap(background_color, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).to_excel('Styled_Basic_EPS.xlsx', 'EPS_Basic', engine='openpyxl')
df_eps.style.applymap(color_white, subset=pd.IndexSlice[:, columns_name]).applymap(background_color, subset=pd.IndexSlice[:, columns_name]).applymap(font_family).applymap(font_size).to_excel('Styled_Basic_Perspective_EPS.xlsx', 'EPS_Basic', engine='openpyxl')

# Pandas style function to hignlight specific columns
# http://pandas.pydata.org/pandas-docs/stable/style.html#Finer-Control:-Slicing
# Finer Control: Slicing
# ex: df.style.apply(highlight_max, subset=['B', 'C', 'D'])

['Growth_108Q1', '2QMAGrowth_108Q1', 'Growth_107Q4', '2QMAGrowth_107Q4', 'Growth_107Q3', '2QMAGrowth_107Q3', 'Growth_107Q2', '2QMAGrowth_107Q2', 'Growth_107Q1', '2QMAGrowth_107Q1', 'Growth_106Q4', '2QMAGrowth_106Q4', 'Growth_106Q3', '2QMAGrowth_106Q3', 'Growth_106Q2', '2QMAGrowth_106Q2']


C:\ProgramData\Anaconda2\lib\site-packages\pandas\core\indexing.py:1472: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)
